In [33]:
import pandas as pd
import numpy as np
from datetime import timedelta
import datetime as dt
import plotly.graph_objects as go

import warnings
warnings.filterwarnings("ignore")

import os
import pickle
from config import BASE_DIR
print(os.getcwd())
os.chdir(BASE_DIR)
import scripts.functions as fn 

from scripts.indicators import resample, zigzag, fibonacci_retroceso, fibonacci_extension

from binance.client import Client


C:\Users\lbisa\Mi unidad (leonardo.bisaro@gmail.com)\Cripto\python\trd_app


In [34]:
#Funcion para descarga de velas
def get_klines(symbol,interval,start,end):
    print(symbol, interval, start, end )
    df = client.get_historical_klines(symbol=symbol, interval=interval, start_str=start, end_str=end)
    df = pd.DataFrame(df)
    df = df.iloc[:, :6]
    df.columns = ["datetime", "open", "high", "low", "close", "volume"]
    df['open'] = df['open'].astype('float')
    df['high'] = df['high'].astype('float')
    df['low'] = df['low'].astype('float')
    df['close'] = df['close'].astype('float')
    df['volume'] = df['volume'].astype('float')
    df['datetime'] = pd.to_datetime(df['datetime'], unit='ms') - dt.timedelta(hours=3)
    #df=df.set_index('datetime')
    return df

In [35]:
environment = 'klines'
#environment = 'binance'

if environment == 'klines':

	klines_file  = './backtest/klines/0m01/Completo_BTCUSDT_0m01_2021-01-01_2023-07-31.DataFrame'
	with open(klines_file, 'rb') as file:
		df = pickle.load(file)
		#df.set_index('datetime',inplace=True)

	df = resample(df,(60))
else:
	#Conexion con Binance sin API-KEY
	client = Client()

	start = '2024-11-01'
	end = '2024-11-24'
	symbol = 'BTCUSDT'
	interval = '1h'
	real_start = (dt.datetime.strptime(start, "%Y-%m-%d") ).strftime("%Y-%m-%d")
	real_end = (dt.datetime.strptime(end, "%Y-%m-%d") ).strftime("%Y-%m-%d")
	utc_start = real_start+' 00:00:00'
	utc_end = real_end+' 23:59:59'
	df = get_klines(symbol=symbol,interval=interval, start=utc_start,end=utc_end)


#df = fn.ohlc_mirror_v(df)

#Filtrar rango de fechas
#ini = pd.to_datetime('2018-06-26')
#fin = pd.to_datetime('2028-05-01')
#df = df[(df['datetime']>=ini)&(df['datetime']<=fin)]
#df.reset_index(inplace=True)
#df.drop(columns=['index'],inplace=True)

#df.drop(columns=['volume'],inplace=True)

#Quitar parte del dataframe
#df = df[500:1500]
#df.reset_index(inplace=True)
#df.drop(columns=['index'],inplace=True)

In [36]:
def pivots_acum(df,column):
	last = 0
	for i,r in df.iterrows():
		if r[column] > 0:
			df.at[i,column] = r[column]+last
			last = r[column]+last
		else:
			last = 0
	return df


In [37]:
df['price'] = df['close']

#Definir pivots
df = zigzag(df, resample_periods=24*3)

pivots = df[df['ZigZag']>0].copy()
pivots['side'] = np.where((pivots['ZigZag']>pivots['ZigZag'].shift()),1,-1)
first_pivot_index = pivots.index[0]
pivots.at[first_pivot_index,'side'] = 0 #El primer pivot no se puede definir por lo tanto queda neutro 

#Se almacena el precio del pivot anterior
pivots['ZigZag_1'] = pivots['ZigZag'].shift(1)
pivots['ZigZag_2'] = pivots['ZigZag_1'].shift(1)

#Separar pivots en maximos y minimos
pivots['maxs'] = np.where((pivots['side']>0), pivots['ZigZag'],None)
maxs = pivots[pivots['maxs']>0].copy()
pivots['mins'] = np.where((pivots['side']<0), pivots['ZigZag'],None)
mins = pivots[pivots['mins']>0].copy()

#Acumular maximos crecientes
maxs['maxs_up'] = np.where(maxs['ZigZag']>maxs['ZigZag'].shift(1),1,0)
maxs = pivots_acum(maxs,'maxs_up')

#Acumular minimos crecientes
mins['mins_up'] = np.where(mins['ZigZag']>mins['ZigZag'].shift(1),1,0)
mins = pivots_acum(mins,'mins_up')

#Acumular maximos decrecientes
maxs['maxs_down'] = np.where(maxs['ZigZag']<maxs['ZigZag'].shift(1),1,0)
maxs = pivots_acum(maxs,'maxs_down')

#Acumular minimos decrecientes
mins['mins_down'] = np.where(mins['ZigZag']<mins['ZigZag'].shift(1),1,0)
mins = pivots_acum(mins,'mins_down')

#Incorporar los calculos de maximos y minimos al DF de pivots
pivots['maxs_up'] = None
pivots['maxs_down'] = None
for index, row in maxs.iterrows():
	pivots.at[index,'maxs_up'] = row['maxs_up']
	pivots.at[index,'maxs_down'] = row['maxs_down']
pivots['mins_up'] = None
pivots['mins_down'] = None
for index, row in mins.iterrows():
	pivots.at[index,'mins_up'] = row['mins_up']
	pivots.at[index,'mins_down'] = row['mins_down']
pivots['maxs_up'].ffill(inplace=True)
pivots['maxs_down'].ffill(inplace=True)
pivots['mins_up'].ffill(inplace=True)
pivots['mins_down'].ffill(inplace=True)

#Completando el datafamr principal con los datos de pivots
df_cols = df.columns.copy()
for col in pivots.columns:
	if not col in df_cols:
		df[col]=None
for index, row in pivots.iterrows():
	for col in pivots.columns:
		if not col in df_cols:
			df.at[index,col] = row[col]

df['side'].ffill(inplace=True)
df['maxs_up'].ffill(inplace=True)
df['maxs_down'].ffill(inplace=True)
df['mins_up'].ffill(inplace=True)
df['mins_down'].ffill(inplace=True)

In [38]:
df_to_show = df #[0:20]
#df_to_show = HeikinAshi(df_to_show)
#df_to_show['close'] = df_to_show['HA_close']
#df_to_show['open'] = df_to_show['HA_open']
#df_to_show['high'] = df_to_show['HA_high']
#df_to_show['low'] = df_to_show['HA_low']
#df_to_show.drop(columns=['price'],inplace=True)
indicators = [
     {'col': 'ZigZag','name': 'ZigZag','color': 'gray','row': 1, 'mode':'lines',},
     #{'col': 'mins','name': 'mins','color': 'red','row': 1, 'mode':'markers',},
     #{'col': 'long','name': 'long','color': 'green','row': 1, 'mode':'lines',},
     #   {'col': 'FL_0.0%', 'name': 'FL_0.0%', 'color': 'red', 'row': 1, 'mode': 'lines', }, 
     #   {'col': 'FL_gold1', 'name': 'FL_gold1', 'color': 'orange', 'row': 1, 'mode': 'lines', }, 
     #   {'col': 'FL_gold2', 'name': 'FL_gold2', 'color': 'orange', 'row': 1, 'mode': 'lines', }, 
     #   {'col': 'FL_100.0%', 'name': 'FL_100.0%', 'color': 'green', 'row': 1, 'mode': 'lines', }, 
        ]

indicators_out = [
     {'col': 'side','name': 'side','color': 'yellow','row': 1, 'mode':'lines',},
     {'col': 'maxs_up','name': 'maxs_up','color': 'green','row': 2, 'mode':'lines',},
     {'col': 'maxs_down','name': 'maxs_up','color': 'red','row': 2, 'mode':'lines',},
     {'col': 'mins_up','name': 'mins_up','color': 'green','row': 3, 'mode':'lines',},
     {'col': 'mins_down','name': 'mins_up','color': 'red','row': 3, 'mode':'lines',},
     
        ]

#https://plotly.com/python/reference/scatter/#scatter-marker-symbol
events = [
       #{'df':df_to_show,'col':'buy','name': 'BUY','color': 'green','symbol': 'triangle-up' }, 
       #{'df':df_to_show,'col':'sell','name': 'SELL','color': 'red','symbol': 'triangle-down' }, 
     ]


fig = fn.ohlc_chart(df_to_show,indicators=indicators,indicators_out=indicators_out,events=events,) 
fig.show()

